## libraries
Google drive mount

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
# libraries
import requests
import os
import pickle
import re
import pandas as pd
from tqdm.notebook import tqdm
import ast
from IPython.display import clear_output
import matplotlib.pyplot as plt
import seaborn as sns

## load data

In [ ]:
file_path = '/your_path'

In [1]:
# 키워드 추출된 review 데이터셋 로드
# csv로 load시
review = pd.read_csv(file_path+'/file_name.csv')  # csv로 load시
review['keywords_ug'] = review['keywords_ug'].apply(lambda x : ast.literal_eval(x))  # 리스트 형태로 변환해줘야 함
review['keywords_bg'] = review['keywords_bg'].apply(lambda x : ast.literal_eval(x))

In [ ]:
# json으로 load시
review = pd.read_json(file_path+'/file_name.json', lines=True)  # 별도 변환 필요 없음

## Extract Topics by openAI API

In [ ]:
!pip install openai
from openai import OpenAI
clear_output()

### test

In [ ]:
# 1개 케이스 테스트 해보기
keywords = [ 'stars', 'tchopstix', 'dining', 'order', 'sushi', 'vegetables', 'server', 'sushi', 'rice', 'sauces', 'roll', 'street', 'reviews', 'sushi', 'express', 'healthy', 'tea', 'strawberry', 'vanilla']

prompt = f"""Keyword List : {set(keywords)}
        These keywords are related to the review of restaurants or food category.
        You have to work on the following requirements:
        1. Group keywords in Keyword List based on similarity. *Every keyword must belong to a topic*.
        2. Name each group and make it the upper topic.
        3. Consider fixed topics for suggested categories, like 'food', 'service', 'atmosphere'.
         - food : such as food, beverage related to menu, taste and nutritional values.
         - service : such as assistance, benefits, duties, delivery, parking, utility, appropriateness, and courtesy related to cumstomer experiment.
         - atmosphere : overall environment such as dining space, mood, interior furniture, lighting, outdoor dining, terrace etc.
         For any keywords not related to these topics, feel free to categorize them as you see fit.
        4. especially, any keywords that seem related to store names, reviews, or stars are not included in the fixed topics;
           instead, they are included in 'Others'
        5. After naming, return the text in Python dictionary format : key is topic, values are keywords
        """

api_key = "your_key" # API key 발급
client = OpenAI(api_key=api_key)

response = client.chat.completions.create(
    model="gpt-3.5-turbo",  # 빠른 text 추출을 위해 3.5 turbo 사용(+비용 문제..)
    response_format={ "type": "text" },
    messages=[
        {"role": "user", "content": prompt},])

test = response.choices[0].message.content
print(test)

{
    "food": ["tea", "vegetables", "sushi", "roll", "vanilla", "rice", "sauces", "strawberry"],
    "service": ["server", "order", "express"],
    "atmosphere": ["dining", "street"],
    "others": ["stars", "tchopstix", "healthy", "reviews"]
}


### extract

In [ ]:
# 결과 담을 리스트 생성
result = []

In [ ]:
# 중간에 끊기면 pickle 파일 다시 load
with open(file_path+'/topics.pkl', 'rb') as file :
  result = pickle.load(file)
len(result)

In [ ]:
api_key = 'your_key'

start, end = 0, len(review)  # 필요시 끊어서 설정

with tqdm(total=end-start) as pbar :
  for idx, row in review.loc[start:end, :].iterrows() :
    if idx - start < len(result) : # 이미 추출했으면 pass
      pbar.update(1)
      continue
    else:
      prompt = f"""Keyword List: {(row['keywords_bg'])}
          These keywords are related to the review of restaurants or food category.
          You have to work on the following requirements:
          1. Group keywords in Keyword List based on similarity. *Every keyword must belong to a topic*.
          2. Name each group and make it the upper topic.
          3. Consider fixed topics for suggested categories, like 'food', 'service', 'atmosphere', 'facility', 'price', and 'others'.
            - food: Keywords related to menu items to eat, taste, beverages, and nutritional values.
            - service: Keywords related to customer comport and assistance, delivery(i.e. 'deli', 'uber'), utilities, appropriateness, and courtesy in operation.
            - atmosphere: Keywords related to the overall dining environment and mood, including interior design, furniture, lighting, and outdoor spaces.
            - facility: Keywords related to the physical amenities of the restaurant, such as cleanliness, parking, restrooms and equipment.
            - price: Keywords related to the cost, pricing, value for money, affordability, and overall expense of the dining experience.
            - others: Keywords that don't fit into the above categories, especially those related to store names, reviews, or star ratings.
          4. After naming, return the text in Python dictionary format: keys are topics, values are keywords. *Set values in list type*
          5. If some topic hasn't any keyword, *Don't include that topic key in dictionary*.
          """

      client = OpenAI(api_key=api_key)

      response = client.chat.completions.create(
        model="gpt-3.5-turbo",
        response_format={ "type": "text" },
        messages=[
            {"role": "user", "content": prompt},])

      temp = response.choices[0].message.content.strip()
      result.append({row['review_id']: temp})

      # 20개씩 저장
      if len(result)%20 == 0 :
        with open(file_path + '/topics.pkl', 'wb') as file :
          pickle.dump(result, file)
      pbar.update(1)
  # 끝나고 저장
  with open(file_path + '/topics.pkl', 'wb') as file :
    pickle.dump(result, file)

## Post Processing
* text형식으로 추출하다보니 형식에 맞지 않는 case들 후처리 필요해짐

In [ ]:
# 필요 시 로드
with open(file_path + '/topics.pkl', 'rb') as file :
  topic = pickle.load(file)

# 런타임 살아있으면 변수할당
# topic = result

In [ ]:
# 예외처리할 case들 변환해주기
def postprocessing(topic, post_topic) :
  for i in range(len(topic)) :
    key = list(topic[i].keys())[0]
    values = list(topic[i].values())[0]
    values = re.sub('\n','',values)   # 줄바꿈 기호 모두 제거
    try:
      post_topic[key] = ast.literal_eval(values)
    except Exception as e:
      try:
        # key가 문자열로 안 들어가 있어서(''로 안묶임) 에러남
        values = re.sub(r"(\w+\s*\w*):", r"'\1':", values)
        # didn't나 ''처럼 작은따옴표가 중첩되는 경우도 오류남 후...
        values = re.sub(r"(\w)\'(\w)", r"\1\2", values)
        # 이상하게 코드로 들어간 경우
        values = re.sub(r'^```python|```$', '', values)
        # 왜 대괄호로 안 묶여있니..
        if ('{' not in values) or ('}' not in values):
          values = '{'+ values +'}'
        # 콤마로 구분 안 되어 있으면...
        if '],' not in values :
          values = re.sub(r"(\])\s*(\')", r"\1,\2", values)
        post_topic[key] = ast.literal_eval(values)
      # 위 case들 해당 안 되면 error
      except Exception as e:
        post_topic[key] = {'error':e}
        # break
  return post_topic

* 1차 후처리

In [ ]:
# 리뷰 id와 매핑할 딕셔너리 생성
post_topic = {}
post_topic = postprocessing(topic, post_topic)
len(post_topic)

30880

In [ ]:
post_topic

{1443659: {'service': ['deli uber'], 'others': ['check person']},
 1044648: {'food': ['creme brulee',
   'hh dishes',
   'blueberry mojito',
   'asian nachos',
   'entree'],
  'facility': ['parking sux'],
  'others': ['nice feel',
   'brunch great',
   'bar area',
   'dinner good',
   'place celebrate']},
 5693786: {'others': ['logo restaurant'],
  'facility': ['open 24'],
  'food': ['menu breakfast']},
 1166589: {'service': ['servers watched',
   'group slow',
   'came group',
   'going slooooww'],
  'food': ['running food', 'food okay'],
  'others': ['felt bad']},
 6678286: {'food': ['bags chips', 'tasty good', 'philly club'],
  'service': ['deli', 'come hungry'],
  'others': ['yuge']},
 2462810: {'service': ['order waited', 'worst service'],
  'food': ['going cheddars'],
  'facility': ['cleaning 8pm']},
 2725854: {'food': ['great steaks',
   'steaks rib',
   'enjoyed fries',
   'taste beef',
   'meat prime',
   'steak house'],
  'service': ['service good', 'knows doing', 'beef servi

* 2차 후처리

In [ ]:
# 위에서 error 난 case들 따로 살펴보기
error_id = []
for id, tops in post_topic.items() :
  if list(post_topic[id].keys())[0] == 'error':
    error_id.append(id)
print(len(error_id))

In [ ]:
error_id

[6503328, [1723154, 4123109, 1739912, 2483163, 401869, 6268559]]

In [ ]:
# 1) keyword가 topic에 배정 안 된 경우
sorted([6503328, 4123109,1739912, 2483163, 401869])

# 2) 키워드들이 모두 쪼개진 경우 : 1460566 ~ 475723
error_id[2:22]
# ===> 다시 뽑기

# 3) 앞뒤로 ```로 묶인 경우
# 4) 작은 따옴표 2개 묶인 경우('')
# ===> 정규식으로 처리

In [ ]:
re_topic = []

for idx, row in review.iterrows() :
    if row['review_id'] in error_id:
      prompt = f"""Keyword List: {(row['keywords_bg'])}
          These keywords are related to the review of restaurants or food category.
          You have to work on the following requirements:
          1. Group keywords in Keyword List based on similarity. *Every keyword must belong to a topic*.
          2. Name each group and make it the upper topic.
          3. Consider fixed topics for suggested categories, like 'food', 'service', 'atmosphere', 'facility', 'price', and 'others'.
            - food: Keywords related to menu items to eat, taste, beverages, and nutritional values.
            - service: Keywords related to customer comport and assistance, delivery(i.e. 'deli', 'uber'), utilities, appropriateness, and courtesy in operation.
            - atmosphere: Keywords related to the overall dining environment and mood, including interior design, furniture, lighting, and outdoor spaces.
            - facility: Keywords related to the physical amenities of the restaurant, such as cleanliness, parking, restrooms and equipment.
            - price: Keywords related to the cost, pricing, value for money, affordability, and overall expense of the dining experience.
            - others: Keywords that don't fit into the above categories, especially those related to store names, reviews, or star ratings.
          4. After naming, return the text in Python dictionary format: keys are topics, values are keywords. *Set values in list type*
          5. If some topic hasn't any keyword, *Don't include that topic key in dictionary*.
          """
      client = OpenAI(api_key=api_key)

      response = client.chat.completions.create(
        model="gpt-3.5-turbo",
        response_format={ "type": "text" },
        messages=[
            {"role": "user", "content": prompt},])

      temp = response.choices[0].message.content.strip()
      re_topic.append({row['review_id']: temp})
re_topic

[{1278962: "{\n    'others': ['review ice', 'window workers', 'extremely disappointed'],\n    'service': ['closing early'],\n    'atmosphere': ['sad'],\n    'food': ['minutes close'],\n    'others': ['hope']\n}"},
 {6112977: '{\n    "food": ["ordered calzone", "calzone pretty", "hit spot", "cheese fries", "haven\'t tried"],\n    "service": ["order greeted"],\n    "others": ["asian supermarket", "sure soon"]\n}'},
 {3394205: "{\n    'food': ['fried cod', 'food keeps'],\n    'service': ['staff friendly'],\n    'atmosphere': ['atmosphere cool'],\n    'others': ['honey pit']\n}"},
 {4681402: "{\n    'food': ['sunrise margaritas'],\n    'others': ['place chilis', 'bad experience', 'coming chilis'],\n    'facility': ['bathrooms nice']\n}"},
 {2715842: '{\n    "food": ["roast croissant", "delicious", "cbd options"],\n    "others": ["way town", "barista kind", "local definitely"]\n}'},
 {1306218: "{\n    'food': ['chargrilled oysters'],\n    'others': ['ladies fantastic', 'hour celebrate', 'co

In [ ]:
# 다시 추출한 topic도 후처리
post_topic = postprocessing(re_topic, post_topic)
len(post_topic)

30880

* 3차 후처리

In [ ]:
# case 1) topic에 keyword 없는 애들(빈 topic)
# case 2) 모든 문자열이 쪼개진 아이들(결과 참고)
post_topic[6112977]

{'food': ['v', 'e', 'n', 'y', 'u', 'p', 'z', 'h', 'l', 'a', 'k'],
 'atmosphere': ['r', 's'],
 'facility': [',', 'f', 'd', 'o'],
 'others': ['[', ']']}

In [ ]:
# case 1) 빈 topic 제거
for key, val in post_topic.items():
  for k in list(val.keys()):
    if not val[k] or (isinstance(val[k], list) and '' in val[k]):  # 빈 값이거나 빈 문자열을 가졌을 때
      val.pop(k)

In [ ]:
# case2) 후처리할 인덱스(리뷰id) 담을 리스트
filtered_indices = []

# 필터링 조건을 검사하는 함수
def is_invalid_topic(post_topic):
  for key, values in post_topic.items():
    if any(len(value.strip()) <= 1 for value in values):  # 공백이거나 길이가 1 이하인(쪼개진) 항목이 있는지 검사
      return True
    if not values:  # 빈 리스트인 경우
      return True
    if any(char in values for char in ['[', ']', "'", ",", " "]):  # 특수문자가 있는지 검사
      return True
  return False

for key, val in post_topic.items():
  if is_invalid_topic(val) :
    filtered_indices.append(key)

print("Filtered Indices:", filtered_indices)

In [ ]:
re_topic = []

for idx, row in review.iterrows() :
    if row['review_id'] in filtered_indices :
      prompt = f"""Keyword List: {(row['keywords_bg'])}
          These keywords are related to the review of restaurants or food category.
          You have to work on the following requirements:
          1. Group keywords in Keyword List based on similarity. *Every keyword must belong to a topic*.
          2. Name each group and make it the upper topic.
          3. Consider fixed topics for suggested categories, like 'food', 'service', 'atmosphere', 'facility', 'price', and 'others'.
            - food: Keywords related to menu items to eat, taste, beverages, and nutritional values.
            - service: Keywords related to customer comport and assistance, delivery(i.e. 'deli', 'uber'), utilities, appropriateness, and courtesy in operation.
            - atmosphere: Keywords related to the overall dining environment and mood, including interior design, furniture, lighting, and outdoor spaces.
            - facility: Keywords related to the physical amenities of the restaurant, such as cleanliness, parking, restrooms and equipment.
            - price: Keywords related to the cost, pricing, value for money, affordability, and overall expense of the dining experience.
            - others: Keywords that don't fit into the above categories, especially those related to store names, reviews, or star ratings.
          4. After naming, return the text in Python dictionary format: keys are topics, values are keywords. *Set values in list type*
          5. If some topic hasn't any keyword, *Don't include that topic key in dictionary*.
          """
      client = OpenAI(api_key=api_key)

      response = client.chat.completions.create(
        model="gpt-3.5-turbo",
        response_format={ "type": "text" },
        messages=[
            {"role": "user", "content": prompt},])

      temp = response.choices[0].message.content.strip()
      re_topic.append({row['review_id']: temp})
re_topic

In [ ]:
# 다시 추출한 topic도 후처리
post_topic = postprocessing(re_topic, post_topic)
len(post_topic)

In [ ]:
# pickle로 저장
with open( file_path + '/post_topic.pkl', 'wb') as file :
  pickle.dump(post_topic, file)

### Add Column

In [ ]:
# review_id로 매핑하여 컬럼 추가
review['topics_raw'] = review['review_id'].map(topic)  # gpt로 뽑은 raw text
review['topics'] = review['review_id'].map(post_topic) # 정제한 topic 딕셔너리

# topic 순서 조정
ordered_key = ['food','service','atmosphere','facility','price','others']

review['topics'] = review['topics'].map(lambda d : {key: d[key] for key in ordered_key if key in d}  )
review['topics']

## with Sentiment Data
* roberta로 감성분석한 df에 문장별 keyword, topic 매핑하여 컬럼 추가

### Add Columns


In [ ]:
roberta = pd.read_csv(file_path + '/file_name.csv')  # encoding = 'ISO-8859-1'
roberta

review_id  stars                                           sentence  \
0         1443659      5    Found 51st Deli on Uber Eats and we loved it!!!   
1         1443659      5            I can't wait to check it out in person!   
2         1044648      5  Love love love this place for HH n dinner is g...   
3         1044648      5  Its ok for brunch, not as great as what people...   
4         1044648      5       The Asian Nachos are the dish to get for HH.   
...           ...    ...                                                ...   
224195    5916423      1                                     Won't go back.   
224196    1847631      5                      Coma is my go to coffee shop.   
224197    1847631      5  Their food and beverages are consistently deli...   
224198    1847631      5  Online ordering is super easy or you can go in...   
224199    1847631      5                                  Highly recommend!   

        compound_score  positive_score  neutral_score  negative_score  \
0             0.989771        0.991007       0.007758        0.001236   
1             0.985175        0.986700       0.011776        0.001525   
2             0.989841        0.991794       0.006252        0.001954   
3            -0.041061        0.229077       0.500784        0.270139   
4             0.397284        0.408822       0.579640        0.011538   
...                ...             ...            ...             ...   
224195       -0.121095        0.092444       0.694016        0.213540   
224196        0.906624        0.908743       0.089138        0.002119   
224197        0.985733        0.987232       0.011269        0.001499   
224198        0.910056        0.912051       0.085953        0.001995   
224199        0.944857        0.947948       0.048961        0.003091   

       keywords_ug       keywords_bg       topic  
0             uber         deli uber     service  
1             wait      check person      others  
2           dinner       dinner good      others  
3           brunch      brunch great      others  
4           nachos      asian nachos        food  
...            ...               ...         ...  
224195         won               won      others  
224196      coffee       coma coffee  atmosphere  
224197       dairy  vegan vegetarian        food  
224198       order   online ordering     service  
224199   recommend  highly recommend      others  

[224200 rows x 10 columns]

In [ ]:
cols = ['review_id', 'sentence', 'keywords_ug', 'keywords_bg', 'topic']
data = {col: [] for col in cols}

with tqdm(total=len(review)) as pbar :
  for idx, row in review.iterrows():
    row['keywords_ug'] = ast.literal_eval(row['keywords_ug'])
    row['keywords_bg'] = ast.literal_eval(row['keywords_bg'])
    row['sentences'] = ast.literal_eval(row['sentences'])
    for col in cols :
      if col == 'review_id':
        # int는 list로 감싸줘야 extend 가능
        # 문장 수만큼 review_id 반복 추가
        data[col].extend([row[col]]*len(row['sentences']))
      # topics는 dict 타입으로 각 keyword가 포함된 topic을 순서대로 담음
      elif col == 'topics' :
        topics = row[col] # 토픽dict
        for kw in row['keywords_bg'] :
          assigned_topic = None   # 할당된 토픽 초기화
          for key, val in topics.items():
            if kw in val :
              assigned_topic = key
              break # 찾으면 다른 토픽 찾기 멈춤
          if assigned_topic :
              data[col].append(assigned_topic)
          else: # 할당된 토픽 없으면..?
              data[col].append(None)
      else : # id, topic 제외한 컬럼들
        if isinstance(data[col], list) :
          data[col].extend(row[col])
        else :
          data[col].append(row[col])
    pbar.update(1)

kw_topic_df = pd.DataFrame(data)
kw_topic_df

  0%|          | 0/30880 [00:00<?, ?it/s]

review_id                                          sentences  \
0         1443659    Found 51st Deli on Uber Eats and we loved it!!!   
1         1443659            I can't wait to check it out in person!   
2         1044648  Love love love this place for HH n dinner is g...   
3         1044648  Its ok for brunch, not as great as what people...   
4         1044648       The Asian Nachos are the dish to get for HH.   
...           ...                                                ...   
228492    5916423                                     Won't go back.   
228493    1847631                      Coma is my go to coffee shop.   
228494    1847631  Their food and beverages are consistently deli...   
228495    1847631  Online ordering is super easy or you can go in...   
228496    1847631                                  Highly recommend!   

       keywords_ug       keywords_bg      topics  
0             uber         deli uber     service  
1             wait      check person      others  
2           dinner       dinner good      others  
3           brunch      brunch great      others  
4           nachos      asian nachos        food  
...            ...               ...         ...  
228492         won               won      others  
228493      coffee       coma coffee  atmosphere  
228494       dairy  vegan vegetarian        food  
228495       order   online ordering     service  
228496   recommend  highly recommend      others  

[228497 rows x 5 columns]

In [ ]:
review = review[~(review['review_id']==4344482)]  # 중국어 리뷰 삭제
kw_topic_df = kw_topic_df[~(kw_topic_df['review_id']==4344482)]
kw_topic_df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 228496 entries, 0 to 228496
Data columns (total 5 columns):
 #   Column       Non-Null Count   Dtype 
---  ------       --------------   ----- 
 0   review_id    228496 non-null  int64 
 1   sentence     228496 non-null  object
 2   keywords_ug  228496 non-null  object
 3   keywords_bg  228496 non-null  object
 4   topic        219889 non-null  object
dtypes: int64(1), object(4)
memory usage: 10.5+ MB


In [ ]:
# roberta df에 합치기
kw_top_filter = kw_topic_df[['keywords_ug','keywords_bg','topic']]

roberta.reset_index(drop=True, inplace=True)
kw_top_filter.reset_index(drop=True, inplace=True)

concat_df = pd.concat([roberta, kw_top_filter], axis=1)
concat_df

review_id  stars                                           sentence  \
0         1443659    5.0    Found 51st Deli on Uber Eats and we loved it!!!   
1         1443659    5.0            I can't wait to check it out in person!   
2         1044648    5.0  Love love love this place for HH n dinner is g...   
3         1044648    5.0  Its ok for brunch, not as great as what people...   
4         1044648    5.0       The Asian Nachos are the dish to get for HH.   
...           ...    ...                                                ...   
228491    5916423    1.0                                     Won't go back.   
228492    1847631    5.0                      Coma is my go to coffee shop.   
228493    1847631    5.0  Their food and beverages are consistently deli...   
228494    1847631    5.0  Online ordering is super easy or you can go in...   
228495    1847631    5.0                                  Highly recommend!   

        compound_score  positive_score  neutral_score  negative_score  \
0             0.989771        0.991007       0.007758        0.001236   
1             0.985175        0.986700       0.011776        0.001525   
2             0.989841        0.991794       0.006252        0.001954   
3            -0.041061        0.229077       0.500784        0.270139   
4             0.397284        0.408822       0.579640        0.011538   
...                ...             ...            ...             ...   
228491       -0.121095        0.092444       0.694016        0.213540   
228492        0.906624        0.908743       0.089138        0.002119   
228493        0.985733        0.987232       0.011269        0.001499   
228494        0.910056        0.912051       0.085953        0.001995   
228495        0.944857        0.947948       0.048961        0.003091   

       keywords_ug       keywords_bg       topic  
0             uber         deli uber     service  
1             wait      check person      others  
2           dinner       dinner good      others  
3           brunch      brunch great      others  
4           nachos      asian nachos        food  
...            ...               ...         ...  
228491         won               won      others  
228492      coffee       coma coffee  atmosphere  
228493       dairy  vegan vegetarian        food  
228494       order   online ordering     service  
228495   recommend  highly recommend      others  

[228496 rows x 10 columns]

In [ ]:
concat_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 224200 entries, 0 to 224199
Data columns (total 10 columns):
 #   Column          Non-Null Count   Dtype  
---  ------          --------------   -----  
 0   review_id       224200 non-null  int64  
 1   stars           224200 non-null  int64  
 2   sentence        224200 non-null  object 
 3   compound_score  224194 non-null  float64
 4   positive_score  224194 non-null  float64
 5   neutral_score   224194 non-null  float64
 6   negative_score  224174 non-null  float64
 7   keywords_ug     224199 non-null  object 
 8   keywords_bg     224200 non-null  object 
 9   topic           224200 non-null  object 
dtypes: float64(4), int64(2), object(4)
memory usage: 17.1+ MB


### missing topics

In [ ]:
# topic이 비어있는 경우 발견
missing = concat_df[concat_df['topic'].isna()]
missing

review_id  stars                                           sentence  \
14        5693786    5.0  Unless it was three guys putting their money t...   
151       1564953    4.0  Tough to find good salads in this part of town...   
191       6408608    1.0                               We will not be back.   
262       6124071    5.0        Made our Friday night experience wonderful.   
298       4158750    5.0  I thought that being in Seminole Heights parki...   
...           ...    ...                                                ...   
228361    2358023    5.0                  I ordered Hummus and Babaganoush.   
228362    2358023    5.0  Both came with fresh warm pita wedges in ample...   
228367    6399853    1.0  After never notifying me before I show up to p...   
228467    2367318    3.0         Most of the people stand and drink though.   
228477    2367318    3.0  But as a dining establishment, I didn't partic...   

        compound_score  positive_score  neutral_score  negative_score  \
14           -0.181468        0.031053       0.756426        0.212521   
151           0.967932        0.970039       0.027855        0.002107   
191          -0.602414        0.029966       0.337654        0.632380   
262           0.982624        0.983850       0.014924        0.001226   
298          -0.323043        0.068373       0.540212        0.391416   
...                ...             ...            ...             ...   
228361        0.132698        0.154546       0.823606        0.021848   
228362        0.799628        0.801389       0.196849        0.001762   
228367       -0.766449        0.009753       0.214046        0.776201   
228467       -0.189541        0.042031       0.726397        0.231572   
228477       -0.871973        0.006995       0.114038        0.878967   

       keywords_ug           keywords_bg topic  
14        business              business  None  
151         salads           salads town  None  
191                                       None  
262         friday  experience wonderful  None  
298        parking      seminole heights  None  
...            ...                   ...   ...  
228361      hummus        ordered hummus  None  
228362      wedges           pita wedges  None  
228367     chicken       restaurant hour  None  
228467       stand           stand drink  None  
228477      dining  dining establishment  None  

[7545 rows x 10 columns]

In [ ]:
# 다시 추출
result = []
with tqdm(total=len(missing)) as pbar :
  for idx, row in missing.iterrows() :
    if not row['topic']: # topic이 비어있고
      if row['keywords_bg'] : # keyword가 있으면
        prompt = f""" Please categorize this keyword '{row['keywords_bg']}' into one of these 6 topics.
        topics : food, service, atmosphere, facility, price, others
            - food: Keywords related to menu items to eat, taste, beverages, and nutritional values.
            - service: Keywords related to customer comport and assistance, delivery(i.e. 'deli', 'uber'), utilities, appropriateness, and courtesy in operation.
            - atmosphere: Keywords related to the overall dining environment and mood, including interior design, furniture, lighting, and outdoor spaces.
            - facility: Keywords related to the physical amenities of the restaurant, such as cleanliness, parking, restrooms and equipment.
            - price: Keywords related to the cost, pricing, value for money, affordability, and overall expense of the dining experience.
            - others: Keywords that don't fit into the above categories, especially those related to store names, reviews, or star ratings.
        Just say one of them by topic name.
        """
      else: # keyword 없으면
        prompt = f"""1. Please summarize this sentence between 1-gram and 2-gram : {row['sentence']}
        2. Please categorize this summarized keyword into one of these 6 topics.
        topics : food, service, atmosphere, facility, price, others
            - food: Keywords related to menu items to eat, taste, beverages, and nutritional values.
            - service: Keywords related to customer comport and assistance, delivery(i.e. 'deli', 'uber'), utilities, appropriateness, and courtesy in operation.
            - atmosphere: Keywords related to the overall dining environment and mood, including interior design, furniture, lighting, and outdoor spaces.
            - facility: Keywords related to the physical amenities of the restaurant, such as cleanliness, parking, restrooms and equipment.
            - price: Keywords related to the cost, pricing, value for money, affordability, and overall expense of the dining experience.
            - others: Keywords that don't fit into the above categories, especially those related to store names, reviews, or star ratings.
        3. Return keyword and topic name in tuple format : (keyword, topic)
        """

    client = OpenAI(api_key=api_key)

    response = client.chat.completions.create(
      model="gpt-3.5-turbo",
      response_format={ "type": "text" },
      messages=[
          {"role": "user", "content": prompt},])

    temp = response.choices[0].message.content.strip()

    result.append({idx : [row['review_id'], temp]})
    pbar.update(1)

  0%|          | 0/7545 [00:00<?, ?it/s]

In [ ]:
result

[{14: [5693786, 'Others']},
 {151: [1564953, 'food']},
 {191: [6408608,
   '1. Summarized keyword: not back\n2. Category: others\n3. Tuple format: (not back, others)']},
 {262: [6124071, 'atmosphere']},
 {298: [4158750, 'others']},
 {302: [5518616, 'others']},
 {308: [4524098, 'others']},
 {338: [2385094, 'service']},
 {450: [4601575, 'food']},
 {452: [4601575, 'facility']},
 {485: [209152, 'food']},
 {522: [4143501, 'food']},
 {590: [660439, 'atmosphere']},
 {594: [660439,
   '1. Summarized keyword: "Not much"\n2. Categorized topic: Others\n3. Result: ("Not much", "others")']},
 {602: [660439, 'food']},
 {614: [3485250, 'food']},
 {615: [3485250, 'others']},
 {616: [3485250, 'food']},
 {633: [4066113,
   '1. Summarized keyword: We will be back\n2. Topic: others\n3. Tuple format: (We will be back, others)']},
 {711: [3680804,
   '1. Summarized keyword: go back\n2. Topic: others\n3. Tuple: (go back, others)']},
 {714: [3322390, 'others']},
 {763: [4942479, 'others']},
 {764: [4942479, '

In [ ]:
def extract_and_correct_tuple(text):
  # 튜플 형식을 찾는 정규식 패턴
  match = re.search(r'\(\s*["\']?(.+?)["\']?\s*,\s*["\']?(.+?)["\']?\s*\)', text)
  if match:
    part1 = match.group(1).strip()
    part2 = match.group(2).strip()

    # 따옴표로 이미 묶여 있는지 확인
    if not (part1.startswith("'") or part1.startswith('"')):
      part1 = f'"{part1}"'
    if not (part2.startswith("'") or part2.startswith('"')):
      part2 = f'"{part2}"'
    # 추출한 부분을 따옴표로 묶어줌
    corrected_tuple_str = f"({part1}, {part2})"

    try:
      return ast.literal_eval(corrected_tuple_str)
    except (ValueError, SyntaxError) as e:
      # print(f"Error parsing tuple: {e}")
      return None

  return None

clear_result = []

for r in result:
  for idx, val in r.items():
    if isinstance(val[1], str):  # 문자열인 경우만 처리
      extract = extract_and_correct_tuple(val[1])
      if extract:
        clear_result.append({idx: [val[0], extract]})
      else:
        clear_result.append({idx: [val[0], val[1]]})
    else:
      clear_result.append({idx: val})
clear_result

[{14: [5693786, 'Others']},
 {151: [1564953, 'food']},
 {191: [6408608, ('not back', 'others')]},
 {262: [6124071, 'atmosphere']},
 {298: [4158750, 'others']},
 {302: [5518616, 'others']},
 {308: [4524098, 'others']},
 {338: [2385094, 'service']},
 {450: [4601575, 'food']},
 {452: [4601575, 'facility']},
 {485: [209152, 'food']},
 {522: [4143501, 'food']},
 {590: [660439, 'atmosphere']},
 {594: [660439, ('Not much', 'others')]},
 {602: [660439, 'food']},
 {614: [3485250, 'food']},
 {615: [3485250, 'others']},
 {616: [3485250, 'food']},
 {633: [4066113, ('We will be back', 'others')]},
 {711: [3680804, ('go back', 'others')]},
 {714: [3322390, 'others']},
 {763: [4942479, 'others']},
 {764: [4942479, 'service']},
 {771: [4942479, 'facility']},
 {862: [1164182, 'food']},
 {882: [1164182, ('$8 each', 'price')]},
 {922: [4619744, ('go back', 'others')]},
 {940: [2900385, 'food']},
 {958: [2900385, 'food']},
 {966: [2900385, 'others']},
 {1072: [6221927, 'food']},
 {1085: [1102848, 'food']}

In [ ]:
for res in clear_result:
  for index, value in res.items():
    review_id = value[0]
    if isinstance(value[1], tuple):  # 키워드와 토픽이 모두 주어진 경우
      if len(value[1]) == 2:
        keyword, topic = value[1]
        missing.loc[index, 'keywords_ug'] = keyword  # 적절한 키워드 컬럼 업데이트
        missing.loc[index, 'keywords_bg'] = keyword  # 적절한 키워드 컬럼 업데이트
        missing.loc[index, 'topic'] = topic
      else:
        print(f"Unexpected tuple length at index {index}: {value[1]}")
    else:  # 토픽만 주어진 경우
      topic = value[1]
      missing.loc[index, 'topic'] = topic
missing

review_id  stars                                           sentence  \
14        5693786    5.0  Unless it was three guys putting their money t...   
151       1564953    4.0  Tough to find good salads in this part of town...   
191       6408608    1.0                               We will not be back.   
262       6124071    5.0        Made our Friday night experience wonderful.   
298       4158750    5.0  I thought that being in Seminole Heights parki...   
...           ...    ...                                                ...   
228361    2358023    5.0                  I ordered Hummus and Babaganoush.   
228362    2358023    5.0  Both came with fresh warm pita wedges in ample...   
228367    6399853    1.0  After never notifying me before I show up to p...   
228467    2367318    3.0         Most of the people stand and drink though.   
228477    2367318    3.0  But as a dining establishment, I didn't partic...   

        compound_score  positive_score  neutral_score  negative_score  \
14           -0.181468        0.031053       0.756426        0.212521   
151           0.967932        0.970039       0.027855        0.002107   
191          -0.602414        0.029966       0.337654        0.632380   
262           0.982624        0.983850       0.014924        0.001226   
298          -0.323043        0.068373       0.540212        0.391416   
...                ...             ...            ...             ...   
228361        0.132698        0.154546       0.823606        0.021848   
228362        0.799628        0.801389       0.196849        0.001762   
228367       -0.766449        0.009753       0.214046        0.776201   
228467       -0.189541        0.042031       0.726397        0.231572   
228477       -0.871973        0.006995       0.114038        0.878967   

       keywords_ug           keywords_bg       topic  
14        business              business      Others  
151         salads           salads town        food  
191       not back              not back      others  
262         friday  experience wonderful  atmosphere  
298        parking      seminole heights      others  
...            ...                   ...         ...  
228361      hummus        ordered hummus        food  
228362      wedges           pita wedges        food  
228367     chicken       restaurant hour      others  
228467       stand           stand drink        food  
228477      dining  dining establishment    facility  

[7545 rows x 10 columns]

In [ ]:
concat_df.update(missing) # concat_df에 업데이트

In [ ]:
concat_df = concat_df[concat_df['sentence'].str.len() >= 10] # 10자 이상 문장만 filter

In [ ]:
concat_df['topic'] = concat_df['topic'].apply(lambda x : x.lower())
concat_df['topic'].unique()

array(['service', 'others', 'food', 'facility', 'price', 'atmosphere'],
      dtype=object)

In [ ]:
# 저장
concat_df.to_csv(file_path+'/file_name.csv', index=False)

## One-Hot Encoding

In [ ]:
review = pd.read_csv(file_path+'file_name.csv')

In [ ]:
review['topics'] = review['topics'].apply(lambda x : ast.literal_eval(x) )
review['sentences'] = review['sentences'].apply(lambda x : ast.literal_eval(x) )
review['keywords_bg'] = review['keywords_bg'].apply(lambda x : ast.literal_eval(x) )
review['keywords_ug'] = review['keywords_ug'].apply(lambda x : ast.literal_eval(x) )

In [ ]:
%pip install tensorflow

In [ ]:
from sklearn.preprocessing import OneHotEncoder

* roberta에서 삭제한 문장 review 테이블에서 drop
* roberta에서 추가한 keyword 및 topic도 추가

In [ ]:
roberta_id = roberta.groupby('review_id').agg(
    stars = ('stars', 'mean'),
    sentences = ('sentence', list),
    keywords_ug = ('keywords_ug', list),
    keywords_bg = ('keywords_bg', list),
    topics = ('topic', list),
    compound_score = ('compound_score', "mean"),
    positive_score = ('positive_score',list),
    neutral_score = ('neutral_score',list),
    negagtive_score = ('negative_score', list)
).reset_index()

In [ ]:
keywords_bg_data = {}
keywords_ug_data = {}
topic_data = {}
sentnece_data = {}
compound_scores = {}
for idx, row in roberta_id.iterrows():
  review_id = row['review_id']
  topic = row['topics']
  kw_ug = row['keywords_ug']
  kw_bg = row['keywords_bg']
  cpd = row['compound_score']

  sentnece_data[review_id] = row['sentences']
  keywords_ug_data[review_id] = kw_ug
  keywords_bg_data[review_id] = kw_bg
  topic_data[review_id] = topic
  compound_scores[review_id] = cpd

print(keywords_bg_data, compound_scores, sep = '\n')

{21: ['trying place', 'food ordered', 'place hungry', 'staff friendly'], 507: ['bbq joint', 'way office', 'ribs just', 'sides awesome', 'sauces table', 'ordering works', 'pick meat', 'pick sides', 'slices pie', 'kirkwood food'], 784: ['eat gullifty', 'bar', 'occasional sandwich', 'recently changed', 'pub food', 'mediocre', 'red peppers', 'allergy reasons'], 950: ['pad thai', 'great atmosphere'], 987: ['ambiance good'], 1118: ['soups sandwiches', 'beer soup', 'kids tasted', 'pages place'], 1926: ['valhalla bakery', 'excellent choice', 'dairy free', 'best bakery', 'flavors linger', 'eyes bite', 'moose', 'pastries', 'hour treats', 'pistachio rosewater', 'stuffed cookies', 'cakes definitely', 'cooler', 'bring home', 'vegan cafe'], 2032: ['energy restaurant', 'felt authentic', 'nachos tasted', 'ordered sweating', 'food great'], 2070: ['soup sandwiches', 'fall winter'], 2593: ['business', 'drinks minors', 'make scene', 'bouncer lowlife', 'hostile unprofessional', 'didn care', 'unprofessional

In [ ]:
# roberta df에서 업데이트했던 keywords, topics 반영하여 review df 업데이트
review['topics'] = review['review_id'].map(topic_data)
review['keywords_ug'] = review['review_id'].map(keywords_ug_data)
review['keywords_bg'] = review['review_id'].map(keywords_bg_data)
review['compound_score_mean'] = review['review_id'].map(compound_scores)
review.head()

index  review_id  user_id  business_id  stars  useful  funny  cool  \
0    184    1443659   607521       108373    5.0       0      0     0   
1    207    1044648   182108       134961    5.0       0      0     0   
2    237    5693786   749220        54049    5.0       0      0     0   
3    277    1166589   572170         9263    2.0       1      0     0   
4    323    6678286   816928       108373    5.0       0      0     0   

                                                text                 date  \
0  Found 51st Deli on Uber Eats and we loved it!!...  2017-01-14 21:23:10   
1  Love love love this place for HH n dinner is g...  2017-08-07 23:48:51   
2  Not sure the significance behind the name and ...  2018-09-25 14:49:55   
3  The service is going to be slooooww. And the f...  2017-10-02 01:52:47   
4  Much more than a deli! Wife and I had the Phil...  2017-12-29 20:18:59   

                                           sentences  sentence_counts  \
0  [Found 51st Deli on Uber Eats and we loved it!...                2   
1  [Love love love this place for HH n dinner is ...               11   
2  [Not sure the significance behind the name and...                4   
3  [The service is going to be slooooww., And the...                7   
4  [Much more than a deli!, Wife and I had the Ph...                6   

                                         keywords_ug  \
0                          [deli uber, check person]   
1  [dinner good, brunch great, asian nachos, entr...   
2  [logo restaurant, business, menu breakfast, op...   
3  [going slooooww, food okay, group slow, came g...   
4  [deli, philly club, tasty good, bags chips, co...   

                                         keywords_bg  \
0                          [deli uber, check person]   
1  [dinner good, brunch great, asian nachos, entr...   
2  [logo restaurant, business, menu breakfast, op...   
3  [going slooooww, food okay, group slow, came g...   
4  [deli, philly club, tasty good, bags chips, co...   

                                          topics_raw  \
0  {'service': ['deli uber'], 'others': ['check p...   
1  {'food': ['creme brulee', 'hh dishes', 'bluebe...   
2  {'food': ['menu breakfast'], 'facility': ['ope...   
3  {'food': ['running food', 'food okay'], 'servi...   
4  {'food': ['bags chips', 'tasty good', 'philly ...   

                                              topics  compound_score_mean  
0                                  [service, others]             0.987473  
1  [others, others, food, food, food, food, food,...             0.509072  
2                   [others, others, food, facility]             0.339954  
3  [service, food, service, service, service, oth...            -0.207153  
4               [service, food, food, food, service]             0.257147

In [ ]:
review['sentence_counts'] = review['sentences'].apply(lambda x: len(x))

In [ ]:
review.columns

Index(['index', 'review_id', 'user_id', 'business_id', 'stars', 'useful',
       'funny', 'cool', 'text', 'date', 'sentences', 'sentence_counts',
       'keywords_ug', 'keywords_bg', 'topics_raw', 'topics',
       'compound_score_mean'],
      dtype='object')

In [ ]:
from sklearn.preprocessing import MultiLabelBinarizer

# MultiLabelBinarizer 객체 생성
mlb = MultiLabelBinarizer()

# 원핫 인코딩 수행
df_encoded = pd.DataFrame(mlb.fit_transform(review['topics']), columns=mlb.classes_)

# # 원래 데이터프레임과 결합
review = review.join(df_encoded)

# 결과 출력
new_order = ['index', 'review_id', 'user_id', 'business_id', 'stars', 'useful', 'funny', 'cool', 'text', 'date', 'sentences', 'sentence_counts',
             'keywords_ug', 'keywords_bg', 'compound_score_mean', 'topics_raw', 'topics']
review = review[ new_order + ['food', 'service', 'atmosphere', 'facility', 'price', 'others']]
review

index  review_id  user_id  business_id  stars  useful  funny  cool  \
0          184    1443659   607521       108373    5.0       0      0     0   
1          207    1044648   182108       134961    5.0       0      0     0   
2          237    5693786   749220        54049    5.0       0      0     0   
3          277    1166589   572170         9263    2.0       1      0     0   
4          323    6678286   816928       108373    5.0       0      0     0   
...        ...        ...      ...          ...    ...     ...    ...   ...   
30874  2679757    5143901  1772582        22595    1.0       0      0     0   
30875  2679857    2367318   995712       133866    3.0       8      2     3   
30876  2679863    6085901  1283829        84658    5.0       1      0     2   
30877  2679972    5916423  1410939       123182    1.0       0      0     0   
30878  2680029    1847631   284928        22138    5.0       1      0     0   

                                                    text                 date  \
0      Found 51st Deli on Uber Eats and we loved it!!...  2017-01-14 21:23:10   
1      Love love love this place for HH n dinner is g...  2017-08-07 23:48:51   
2      Not sure the significance behind the name and ...  2018-09-25 14:49:55   
3      The service is going to be slooooww. And the f...  2017-10-02 01:52:47   
4      Much more than a deli! Wife and I had the Phil...  2017-12-29 20:18:59   
...                                                  ...                  ...   
30874  Brand new but filthy. Trash overflowing, dirty...  2021-11-07 23:54:35   
30875  Stopped in for dinner and drinks on a Saturday...  2018-03-25 15:30:29   
30876  Came here for lunch with my girlfriend, place ...  2018-08-10 04:52:50   
30877  Used to go here every week. Won't go again. Ma...  2020-06-03 00:49:05   
30878  Coma is my go to coffee shop. Their food and b...  2021-12-31 17:34:58   

       ...                                        keywords_bg  \
0      ...                          [deli uber, check person]   
1      ...  [dinner good, brunch great, asian nachos, entr...   
2      ...  [logo restaurant, business, menu breakfast, op...   
3      ...  [going slooooww, food okay, group slow, came g...   
4      ...  [deli, philly club, tasty good, bags chips, co...   
...    ...                                                ...   
30874  ...  [brand new, trash overflowing, counter cleanin...   
30875  ...  [stopped dinner, parking sparse, smokers ruini...   
30876  ...               [pancakes, blue berry, fruity drink]   
30877  ...  [used week, won, bag leave, didn food, replace...   
30878  ...  [coma coffee, vegan vegetarian, online orderin...   

       compound_score_mean                                         topics_raw  \
0                 0.987473  {'service': ['deli uber'], 'others': ['check p...   
1                 0.509072  {'food': ['creme brulee', 'hh dishes', 'bluebe...   
2                 0.339954  {'food': ['menu breakfast'], 'facility': ['ope...   
3                -0.207153  {'food': ['running food', 'food okay'], 'servi...   
4                 0.257147  {'food': ['bags chips', 'tasty good', 'philly ...   
...                    ...                                                ...   
30874            -0.604357  {'facility': ['trash overflowing', 'counter cl...   
30875            -0.123799  {'food': ['stopped dinner', 'boyfriend wings',...   
30876             0.681004  {'food': ['pancakes', 'blue berry', 'fruity dr...   
30877            -0.420128  {'food': ['replace meal'], 'service': ['asked ...   
30878             0.936817  {'food': ['vegan vegetarian'], 'service': ['on...   

                                                  topics  food service  \
0                                      [service, others]     0       1   
1      [others, others, food, food, food, food, food,...     1       0   
2                       [others, others, food, facility]     1       0   
3      [service, food, service, servi

In [ ]:
# 최종 저장
review.to_json(file_path+'/file_name.json', orient='records', lines=True)
review.to_csv(file_path+'/file_name.csv',index=False)